# Setup

## Config
Set the tokens based on the numbers in [02-poe-token-count-exploration.ipynb](02-poe-token-count-exploration.ipynb). I like to give a little buffer in-case an explanation goes over.

In [1]:
INPUT_TOKENS = 300
OUTPUT_TOKENS = 1600

INPUT_DATASET = 'derek-thomas/labeled-multiple-choice-explained-mistral-tokenized'
OUTPUT_DATASET = 'derek-thomas/labeled-multiple-choice-explained-mistral-results'
BASE_MODEL = 'mistralai/Mistral-7B-Instruct-v0.3'

# Setup
Here we create the pydantic models for each of our experiments. Note because of how you specify field names in pydantic, we need to use an `alias` and `populate_by_name`. Given that our `Final Answer` is always a letter between a-h we can use an enumeration.

In [2]:
from pydantic import BaseModel, Field
from typing import List
from enum import Enum
import json


class FinalAnswerEnum(str, Enum):
    a = "a"
    b = "b"
    c = "c"
    d = "d"
    e = "e"
    f = "f"
    g = "g"
    h = "h"

class RFAModel(BaseModel):
    reasoning: str = Field(..., alias="Reasoning")
    final_answer: FinalAnswerEnum = Field(..., alias="Final Answer")

    class Config:
        populate_by_name = True
        
class FARModel(BaseModel):
    final_answer: FinalAnswerEnum = Field(..., alias="Final Answer")
    reasoning: str = Field(..., alias="Reasoning")

    class Config:
        populate_by_name = True
        
class FAModel(BaseModel):
    final_answer: FinalAnswerEnum = Field(..., alias="Final Answer")

    class Config:
        populate_by_name = True

We generated lots of experiments in [derek-thomas/labeled-multiple-choice-explained-mistral-tokenized](https://huggingface.co/datasets/derek-thomas/labeled-multiple-choice-explained-mistral-tokenized/viewer?row=0). Now we will aggregate everything we need in `experiments` for convenience.

In [3]:

experiments = {
    'RFA-mistral': {
        'pydantic': RFAModel,
        "lora": "derek-thomas/mistral-v03-poe-RFA-mistral",
        "column": 'user_prompt_RFA',
    },
    'FAR-mistral': {
        'pydantic': FARModel,
        "lora": "derek-thomas/mistral-v03-poe-FAR-mistral",
        "column": 'user_prompt_FAR',
    },
    'RFA-gpt3-5': {
        'pydantic': RFAModel,
        "lora": "derek-thomas/mistral-v03-poe-RFA-gpt3-5",
        "column": 'user_prompt_RFA',
    },
    'FAR-gpt3-5': {
        'pydantic': FARModel,
        "lora": "derek-thomas/mistral-v03-poe-FAR-gpt3-5",
        "column": 'user_prompt_FAR',
    },
    'FA': {
        'pydantic': FAModel,
        "lora": "derek-thomas/mistral-v03-poe-FA",
        "column": 'user_prompt_FA',
    },
    'base': {
        'pydantic': FAModel,
        "lora": None,
        "column": 'user_prompt_FA',
    },
}

LORAS_STRING = ','.join([v['lora'] for _, v in experiments.items() if v and v.get('lora') is not None])
LORAS_STRING

'derek-thomas/mistral-v03-poe-RFA-mistral,derek-thomas/mistral-v03-poe-FAR-mistral,derek-thomas/mistral-v03-poe-RFA-gpt3-5,derek-thomas/mistral-v03-poe-FAR-gpt3-5,derek-thomas/mistral-v03-poe-FA'

In [4]:
from huggingface_hub import login, get_token

# Log in to your Hugging Face account
login()  

In [5]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained(BASE_MODEL, token=get_token())

In [6]:
from datasets import load_dataset

# Load dataset (test split)
dataset = load_dataset(INPUT_DATASET, split='test')
df = dataset.to_pandas()

# Evaluation

## Endpoint Configuration
Im using 8 replicas so I can move quickly! The try/except is in-case I need to make manual changes and I want to load the endpoint.

In [7]:
from huggingface_hub import create_inference_endpoint
from huggingface_hub import get_inference_endpoint


def get_my_endpoint():
    name = f"prompt-order-experiment"
    namespace='derek-thomas'
    try:
        endpoint = get_inference_endpoint(name, namespace=namespace)
    except:
        # Custom Docker image details
        custom_image = {
            "health_route": "/health",
            "url": "ghcr.io/huggingface/text-generation-inference:sha-caff779",  # Needs to be >=2.4.2 to get ordering of json outputs
            "env": {
                "LORA_ADAPTERS": LORAS_STRING,
                "MAX_BATCH_PREFILL_TOKENS": str(20*INPUT_TOKENS),
                "MAX_INPUT_TOKENS": str(INPUT_TOKENS), 
                "MAX_TOTAL_TOKENS": str(INPUT_TOKENS + OUTPUT_TOKENS), 
                "DISABLE_CUSTOM_KERNELS": 'false',
                "MODEL_ID": "/repository"
            },
        }
        
        secrets = {
            "HF_TOKEN": get_token()
        }
        
        # Creating the inference endpoint
        endpoint = create_inference_endpoint(
            name=name,
            namespace=namespace,
            repository='mistralai/Mistral-7B-Instruct-v0.3',
            framework="pytorch",
            accelerator="gpu",
            instance_size="x1",
            instance_type="nvidia-l4",
            region="us-east-1",
            vendor="aws",
            min_replica=8,
            max_replica=8,
            task="text-generation",
            custom_image=custom_image,
            secrets=secrets
        )
            
    print("Your model is ready to use!")
    endpoint.wait()
    return endpoint

In [8]:
%%time
endpoint = get_my_endpoint()

Your model is ready to use!
CPU times: user 21.1 ms, sys: 10 ms, total: 31.1 ms
Wall time: 1.72 s


## Manual Evaluation
Since we havent seen our models in use yet, its a good time to check them out!

### Reasoning Final Answer
In both mistral and gpt3-5 we should see the **Reasoning** first and then the **Final Answer** in the prompt and the responses.

In [9]:
key = 'RFA-mistral'
user_prompt_RFA = df.iloc[0][experiments[key]['column']]
user_prompt_RFA

'<s>[INST] Answer the Question and include your Reasoning and the Final Answer in a json like: {"Reasoning: "...", "Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.\nQuestion: What are busses used for?\nAnswer Choices: (a) Protective shelter (b) Transporting humans (c) Help other species benefit (d) Transporting airplanes (e) A backbone (f) Communication (g) Safe operation (h) Safe driving[/INST]'

In [10]:
response = endpoint.client.text_generation(
    prompt=user_prompt_RFA,
    max_new_tokens=OUTPUT_TOKENS,
    adapter_id=experiments[key]['lora'],
    grammar={"type": "json", "value": experiments[key]['pydantic'].schema()},
)
response

'{"Reasoning": "Busses are primarily used for transporting people, so the correct answer is (b) Transporting humans. The other options are not related to the function of a bus.", "Final Answer": "b"}'

In [11]:
key = 'RFA-gpt3-5'
response = endpoint.client.text_generation(
    prompt=user_prompt_RFA,
    max_new_tokens=OUTPUT_TOKENS,
    adapter_id=experiments[key]['lora'],
    grammar={"type": "json", "value": experiments[key]['pydantic'].schema()},
)
response

'{"Reasoning": "Busses are primarily used for transporting humans, especially in urban areas where public transportation is necessary. They provide a means of transportation for a large number of people at once, reducing traffic congestion and carbon emissions. Therefore, the correct answer is (b) transporting humans.", "Final Answer": "b"}'

### Final Answer Reasoning 
In both mistral and gpt3-5 we should see the **Final Answer** first and then the **Reasoning** in the prompt and the responses.

In [12]:
key = 'FAR-gpt3-5'
user_prompt_FAR = df.iloc[0][experiments[key]['column']]
user_prompt_FAR

'<s>[INST] Answer the Question and include your Final Answer and the Reasoning in a json like: {"Final Answer": "x", "Reasoning: "..."} where x is a letter that corresponds to the answer choice which is a letter between a and h.\nQuestion: What are busses used for?\nAnswer Choices: (a) Protective shelter (b) Transporting humans (c) Help other species benefit (d) Transporting airplanes (e) A backbone (f) Communication (g) Safe operation (h) Safe driving[/INST]'

In [13]:
response = endpoint.client.text_generation(
    prompt=user_prompt_FAR,
    max_new_tokens=575,
    adapter_id=experiments[key]['lora'],
    grammar={"type": "json", "value": experiments[key]['pydantic'].schema()},
)
response

'{"Final Answer": "b", "Reasoning": "Busses are primarily used for transporting humans, especially in urban areas, to facilitate commuting and travel. They are not used for protective shelter, helping other species benefit, transporting airplanes, serving as a backbone, communication, safe operation, or safe driving."}'

In [14]:
key = 'FAR-mistral'
response = endpoint.client.text_generation(
    prompt=user_prompt_FAR,
    max_new_tokens=575,
    adapter_id=experiments[key]['lora'],
    grammar={"type": "json", "value": experiments[key]['pydantic'].schema()},
)
response

'{"Final Answer": "b", "Reasoning": "Busses are primarily used for transporting humans, especially in urban areas, to facilitate their travel from one place to another. The other options are incorrect because busses do not provide protective shelter, do not help other species benefit, are not used to transport airplanes, do not serve as a backbone, are not used for communication, and are not related to safe operation or driving."}'

### Final Answer 
Here we should juse see the **Final Answer** and no **Reasoning**.

In [15]:
key = 'FA'
user_prompt_FA = df.iloc[0][experiments[key]['column']]
user_prompt_FA

'<s>[INST] Answer the Question and include your Final Answer in a json like: {"Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.\nQuestion: What are busses used for?\nAnswer Choices: (a) Protective shelter (b) Transporting humans (c) Help other species benefit (d) Transporting airplanes (e) A backbone (f) Communication (g) Safe operation (h) Safe driving[/INST]'

In [16]:
response = endpoint.client.text_generation(
    prompt=user_prompt_FA,
    max_new_tokens=575,
    adapter_id=experiments[key]['lora'],
)
response

"{'Final Answer': 'b'}"

## Evaluation Loop
I used 20x the prefill than the input and 8 replicas so I should capacity for ~160 parallel requests. Im only using 128 but it should be pretty fast.

In [17]:
import nest_asyncio
import asyncio
from transformers import AutoTokenizer
from tqdm.auto import tqdm

# Allow nested event loops in Jupyter
nest_asyncio.apply()


# Semaphore to limit concurrency
CONCURRENCY_LIMIT = 100 
MAX_NEW_TOKENS = OUTPUT_TOKENS
semaphore = asyncio.Semaphore(CONCURRENCY_LIMIT)

# Progress bar
progress_bar = None  # Global to allow updates from within async functions

# Function to send asynchronous requests to the endpoint
async def fetch_response_async(async_client, prompt, lora_id, pydantic_model):
    async with semaphore:  # Limit the number of concurrent requests
        response = await async_client.text_generation(
            prompt=prompt,
            max_new_tokens=MAX_NEW_TOKENS,
            adapter_id=lora_id if lora_id else None,
            grammar={"type": "json", "value": pydantic_model.schema()}
        )
        progress_bar.update(1)  # Update the progress bar when the request is complete
        return response

# Function to process a single conversation type asynchronously
async def process_conversation_type(conversation_type, model_info, df, tokenizer, async_client):
    response_column = f"responses_{conversation_type.replace('-','_')}"
    responses = []  # Temporary list to hold responses for the current conversation type

    tasks = []
    for _, item in df.iterrows():
        prompt = item.get(model_info["column"])
        tasks.append(fetch_response_async(async_client, prompt, model_info["lora"], model_info["pydantic"]))

    # Wait for all tasks to complete
    responses = await asyncio.gather(*tasks)

    # If responses are strings, use them directly; otherwise, extract 'generated_text'
    try:
        df[response_column] = [resp["generated_text"] for resp in responses]
    except TypeError:  # Fallback in case responses are raw strings
        df[response_column] = responses

# Main function to handle all conversation types
async def main(df, models, tokenizer, async_client):
    global progress_bar
    total_requests = len(df) * len(models)  # Total number of requests across all conversation types
    progress_bar = tqdm(total=total_requests, desc="Processing requests")

    tasks = []
    for conversation_type, model_info in models.items():
        tasks.append(process_conversation_type(conversation_type, model_info, df, tokenizer, async_client))
    await asyncio.gather(*tasks)

    progress_bar.close()  # Close the progress bar when done

# Define parameters and run
# await main(df, experiments, tokenizer, endpoint.async_client)

This is the same as above but with a couple nice features like time-out in case you run into any issues.

In [18]:
import nest_asyncio
import asyncio
from transformers import AutoTokenizer
from tqdm.auto import tqdm
import time

# Allow nested event loops in Jupyter
nest_asyncio.apply()

# Semaphore to limit concurrency
CONCURRENCY_LIMIT = 100 
MAX_NEW_TOKENS = OUTPUT_TOKENS
semaphore = asyncio.Semaphore(CONCURRENCY_LIMIT)

# Progress bar
progress_bar = None  # Global to allow updates from within async functions

# Retry parameters
MAX_RETRIES = 3
BACKOFF_TIME = 2  # Time in seconds before retrying

# Function to send asynchronous requests to the endpoint with retries
async def fetch_response_async(async_client, prompt, lora_id, pydantic_model):
    retries = 0
    while retries < MAX_RETRIES:
        try:
            async with semaphore:  # Limit the number of concurrent requests
                response = await async_client.text_generation(
                    prompt=prompt,
                    max_new_tokens=MAX_NEW_TOKENS,
                    adapter_id=lora_id if lora_id else None,
                    grammar={"type": "json", "value": pydantic_model.schema()}
                )
                progress_bar.update(1)  # Update the progress bar when the request is complete
                return response
        except Exception as e:
            retries += 1
            if retries >= MAX_RETRIES:
                raise e  # If we've exhausted retries, re-raise the error
            else:
                print(f"Error: {e}. Retrying... ({retries}/{MAX_RETRIES})")
                await asyncio.sleep(BACKOFF_TIME)  # Wait before retrying

# Function to process a single conversation type asynchronously
async def process_conversation_type(conversation_type, model_info, df, tokenizer, async_client):
    response_column = f"responses_{conversation_type.replace('-','_')}"
    responses = []  # Temporary list to hold responses for the current conversation type

    tasks = []
    for _, item in df.iterrows():
        prompt = item.get(model_info["column"])
        tasks.append(fetch_response_async(async_client, prompt, model_info["lora"], model_info["pydantic"]))

    # Wait for all tasks to complete
    responses = await asyncio.gather(*tasks)

    # If responses are strings, use them directly; otherwise, extract 'generated_text'
    try:
        df[response_column] = [resp["generated_text"] for resp in responses]
    except TypeError:  # Fallback in case responses are raw strings
        df[response_column] = responses

# Main function to handle all conversation types
async def main(df, models, tokenizer, async_client):
    global progress_bar
    total_requests = len(df) * len(models)  # Total number of requests across all conversation types
    progress_bar = tqdm(total=total_requests, desc="Processing requests")

    tasks = []
    for conversation_type, model_info in models.items():
        tasks.append(process_conversation_type(conversation_type, model_info, df, tokenizer, async_client))
    await asyncio.gather(*tasks)

    progress_bar.close()  # Close the progress bar when done

# Define parameters and run
await main(df, experiments, tokenizer, endpoint.async_client)


Processing requests:   0%|          | 0/10098 [00:00<?, ?it/s]

It took `00:10:43`. Not bad! That should be around `$1.14` total at `$0.80/gpu/hr`.

In [19]:
endpoint.pause()

InferenceEndpoint(name='prompt-order-experiment', namespace='derek-thomas', repository='mistralai/Mistral-7B-Instruct-v0.3', status='paused', url=None)

In [20]:
df_backup = df.copy()

In [21]:
df

topic                                      question_text  \
0        Transportation                          What are busses used for?   
1        Climate change  Which of the following does not contribute to ...   
2           Photography  What uses electrical energy converted from che...   
3          Microbiology                 Bacteria causes what to be harmed?   
4               Biology                         Plants and snakes live _.?   
...                 ...                                                ...   
1678            Biology  New resources required for creation can be red...   
1679            Biology               A drought dehydrates an entire what?   
1680            Biology           An animal requires ingestion to do what?   
1681            Biology                  Ultraviolet light can cause what?   
1682  Physical activity               What can increase a body's strength?   

     answer_key                                   gpt3_5_reasoning  \
0             b  a) Protective shelter: This option is incorrec...   
1             g  a) Nucleus of a cell: This option is not relat...   
2             b  a) Sunlight: Sunlight is a form of energy that...   
3             a  Now, let's go through each option and explain ...   
4             a  b) Important habitats: This option is incorrec...   
...         ...                                                ...   
1678          g  a) Mining: Mining involves extracting minerals...   
1679          d  a) Body water: This option is incorrect becaus...   
1680          e  a) Aerobic capacity: This option is not logica...   
1681          b  a) Ultraviolet light does not cause heat energ...   
1682          c  a) Four limbs: This option is not correct beca...   

                                      mistral_reasoning  \
0     1. Start by reading the question carefully: "C...   
1     To solve this question, let's first understand...   
2     1. Read the question and options carefully: Th...   
3     To answer this question correctly, let's follo...   
4     1. Read the question and options carefully: Th...   
...                                                 ...   
1678  1. Start by reading the question and options c...   
1679  (a) Watershred - This is not a scientific term...   
1680  1. Read the question and options carefully: "W...   
1681  1. First, read the question and options carefu...   
1682  (a) Communication: In this context, the questi...   

                                         answer_choices  \
0     (a) Protective shelter (b) Transporting humans...   
1     (a) Nucleus of a cell (b) Flying in a plane (c...   
2     (a) Sunlight (b) Cameras (c) Cells (d) Buses (...   
3     (a) Plants (b) Electronics (c) Fossils (d) Hum...   
4     (a) Almost everywhere (b) Important habitats (...   
...                                                 ...   
1678  (a) Mining (b) Mutations (c) Fossil fuels (d) ...   
1679  (a) Body water (b) Dried fruit (c) Bodily wate...   
1680  (a) Aerobic capacity (b) Die (c) Water conserv...   
1681  (a) Heat energy (b) Skin cancer (c) Killing in...   
1682  (a) Four limbs (b) Disease (c) Running (d) Bic...   

                                            user_prompt  \
0     Question: What are busses used for?\nAnswer Ch...   
1     Question: Which of the following does not cont...   
2     Question: What uses electrical energy converte...   
3     Question: Bacteria causes what to be harmed?\n...   
4     Question: Plants and snakes live _.?\nAnswer C...   
...                                                 ...   
1678  Question: New resources required for creation ...   
1679  Question: A drought dehydrates an entire what?...   
1680  Question: An animal requires ingestion to do w...   
1681  Question: Ultraviolet light can cause what?\nA...   
1682  Question: What can increase a body's strength?...   

                                        user_prompt_RFA  \
0     <s>[INST] Answer the Question and include your..

In [26]:
def extract_final_answer(response):
    try:
        answer = json.loads(response).get("Final Answer")
    except:
        answer = 'x'
    return answer

# Create new columns for predictions
df['predictions_base'] = df['responses_base'].apply(extract_final_answer)
df['predictions_FA'] = df['responses_FA'].apply(extract_final_answer)
df['predictions_RFA_mistral'] = df['responses_RFA_mistral'].apply(extract_final_answer)
df['predictions_FAR_mistral'] = df['responses_FAR_mistral'].apply(extract_final_answer)
df['predictions_RFA_gpt3_5'] = df['responses_RFA_gpt3_5'].apply(extract_final_answer)
df['predictions_FAR_gpt3_5'] = df['responses_FAR_gpt3_5'].apply(extract_final_answer)


In [28]:
from sklearn.metrics import accuracy_score

print(f"Base: \t\t\t\t\t\t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_base']) * 100, 2)}%")
print(f"Final Answer: \t\t\t\t\t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_FA']) * 100, 2)}%")
print(f"Reasoning and then the Final Answer (Mistral): \t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_RFA_mistral']) * 100, 2)}%")
print(f"Final Answer and then the Reasoning (Mistral): \t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_FAR_mistral']) * 100, 2)}%")
print(f"Reasoning and then the Final Answer (GPT-3.5): \t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_RFA_gpt3_5']) * 100, 2)}%")
print(f"Final Answer and then the Reasoning (GPT-3.5): \t{round(accuracy_score(y_true=df['answer_key'], y_pred=df['predictions_FAR_gpt3_5']) * 100, 2)}%")

Base: 						45.22%
Final Answer: 					64.53%
Reasoning and then the Final Answer (Mistral): 	55.02%
Final Answer and then the Reasoning (Mistral): 	61.79%
Reasoning and then the Final Answer (GPT-3.5): 	57.28%
Final Answer and then the Reasoning (GPT-3.5): 	61.62%


In [29]:
df

topic                                      question_text  \
0        Transportation                          What are busses used for?   
1        Climate change  Which of the following does not contribute to ...   
2           Photography  What uses electrical energy converted from che...   
3          Microbiology                 Bacteria causes what to be harmed?   
4               Biology                         Plants and snakes live _.?   
...                 ...                                                ...   
1678            Biology  New resources required for creation can be red...   
1679            Biology               A drought dehydrates an entire what?   
1680            Biology           An animal requires ingestion to do what?   
1681            Biology                  Ultraviolet light can cause what?   
1682  Physical activity               What can increase a body's strength?   

     answer_key                                   gpt3_5_reasoning  \
0             b  a) Protective shelter: This option is incorrec...   
1             g  a) Nucleus of a cell: This option is not relat...   
2             b  a) Sunlight: Sunlight is a form of energy that...   
3             a  Now, let's go through each option and explain ...   
4             a  b) Important habitats: This option is incorrec...   
...         ...                                                ...   
1678          g  a) Mining: Mining involves extracting minerals...   
1679          d  a) Body water: This option is incorrect becaus...   
1680          e  a) Aerobic capacity: This option is not logica...   
1681          b  a) Ultraviolet light does not cause heat energ...   
1682          c  a) Four limbs: This option is not correct beca...   

                                      mistral_reasoning  \
0     1. Start by reading the question carefully: "C...   
1     To solve this question, let's first understand...   
2     1. Read the question and options carefully: Th...   
3     To answer this question correctly, let's follo...   
4     1. Read the question and options carefully: Th...   
...                                                 ...   
1678  1. Start by reading the question and options c...   
1679  (a) Watershred - This is not a scientific term...   
1680  1. Read the question and options carefully: "W...   
1681  1. First, read the question and options carefu...   
1682  (a) Communication: In this context, the questi...   

                                         answer_choices  \
0     (a) Protective shelter (b) Transporting humans...   
1     (a) Nucleus of a cell (b) Flying in a plane (c...   
2     (a) Sunlight (b) Cameras (c) Cells (d) Buses (...   
3     (a) Plants (b) Electronics (c) Fossils (d) Hum...   
4     (a) Almost everywhere (b) Important habitats (...   
...                                                 ...   
1678  (a) Mining (b) Mutations (c) Fossil fuels (d) ...   
1679  (a) Body water (b) Dried fruit (c) Bodily wate...   
1680  (a) Aerobic capacity (b) Die (c) Water conserv...   
1681  (a) Heat energy (b) Skin cancer (c) Killing in...   
1682  (a) Four limbs (b) Disease (c) Running (d) Bic...   

                                            user_prompt  \
0     Question: What are busses used for?\nAnswer Ch...   
1     Question: Which of the following does not cont...   
2     Question: What uses electrical energy converte...   
3     Question: Bacteria causes what to be harmed?\n...   
4     Question: Plants and snakes live _.?\nAnswer C...   
...                                                 ...   
1678  Question: New resources required for creation ...   
1679  Question: A drought dehydrates an entire what?...   
1680  Question: An animal requires ingestion to do w...   
1681  Question: Ultraviolet light can cause what?\nA...   
1682  Question: What can increase a body's strength?...   

                                        user_prompt_RFA  \
0     <s>[INST] Answer the Question and include your..

In [30]:
from datasets import Dataset, DatasetDict

# Create dataset from df
df.reset_index(drop=True, inplace=True)
dataset = Dataset.from_pandas(df)

# Push dataset to the hub
dataset.push_to_hub(OUTPUT_DATASET)

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/derek-thomas/labeled-multiple-choice-explained-mistral-results/commit/796d0867b715f2fad05d6e54ad1e0e0504ca670c', commit_message='Upload dataset', commit_description='', oid='796d0867b715f2fad05d6e54ad1e0e0504ca670c', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/derek-thomas/labeled-multiple-choice-explained-mistral-results', endpoint='https://huggingface.co', repo_type='dataset', repo_id='derek-thomas/labeled-multiple-choice-explained-mistral-results'), pr_revision=None, pr_num=None)